In [2]:
import bokeh
from bokeh.plotting import figure, show, output_notebook
from bokeh.charts import Scatter, Line, color
from bokeh import palettes
output_notebook()

import numpy as np
import pandas as pd
import os
import math
import time
from IPython.display import clear_output

colors = palettes.Paired12
basedirs = ['/Volumes/dev/structure-experiments/results']

tooltips = [
    ('Experiment', '@experiment'),
    ('Step', '@step'),
    ('Loss', '@loss'),
    ('Prior divergence', '@priordivergence'),
    ('Transition divergence', '@transdivergence'),
]

Loading BokehJS ...

In [3]:
def movingaverage(steps, values, window_size):
    window = np.ones(int(window_size))/float(window_size)

    smooth_values = np.convolve(values, window, 'valid')
    padding = int((len(steps) - len(smooth_values)) / 2)
    aligned_steps = steps[padding : len(steps) - padding]
    return aligned_steps, smooth_values

def sparsify(steps, values, amount):
    if amount < 2: return steps, values
    sparse_steps = []
    sparse_values = []

    for i in range(min(len(steps), len(values))):
        if i % amount == 0:
            sparse_values.append(values[i])
            sparse_steps.append(steps[i])
    return np.array(sparse_steps), np.array(sparse_values)

def parse_result(path):
    df=pd.read_csv(path, error_bad_lines=False)
    for col in df:
        df[col.strip().lower()] = df[col]
#     print(df)
    result = {}
    step_key = "Step" if "Step" in df else 'step'
    steps = df[step_key].values
    for column in df:
        if column != step_key:
            result[column] = (steps, df[column].values)
    return result

def add_result(plot, kind, agent, index):
    fname, legend, columns = agent
    for basedir in basedirs:
        try:
            result = parse_result(os.path.join(basedir, fname))
        except Exception as e:
            print("Error in parsing result:", e)
            continue

    if 'result' not in locals(): return 0
    n_indices = 0
    for i, mode in enumerate(columns):
        mode = mode.strip().lower()
        if mode not in result:
            print("Not found: ", mode)
            continue

        [steps, values] = result[mode]
        if len(steps) == 0:
            continue

        smoothing = -1 # math.floor(len(values) / 5.)
        if smoothing > 1:
            steps, smooth_values = movingaverage(steps, values, smoothing)
        else:
            steps, smooth_values = steps, values

        jitter = 0
        steps = steps + np.random.uniform(-jitter, jitter, len(steps))

        if len(steps) > 200:
            sparse_steps, sparse_values = sparsify(steps, smooth_values, len(steps) // 200)
        else:
            sparse_steps, sparse_values = steps, smooth_values

        if kind == 'circle':
            plot.circle(sparse_steps, 
                        sparse_values,
                        color=colors[(index + i) % len(colors)], 
                        legend=legend + ' ' + mode, 
                        line_color='white', 
                        line_width=0.2)
        else:
            plot.line(sparse_steps, 
                        sparse_values, 
                        color=colors[(index + i) % len(colors)], 
                        line_width=2,
                        legend=legend + ' ' + mode)
        n_indices = i
    return n_indices+1 # int(math.ceil((n_indices + 1) / 2.) * 2)
    
def make_plot(title, results, kind):
    plot = figure(tools='pan,hover,wheel_zoom,box_zoom,save,reset', 
                  active_scroll="wheel_zoom", 
                  plot_width=900,
                  plot_height=600
#                   y_axis_type="symlog"
                 )
    plot.title.text = title
    
    i = 0
    used_colors = {}
    for agent in results:
        _, legend, _ = agent
        if legend not in used_colors:
            used_colors[legend] = i
            i += add_result(plot, kind, agent, i)
        else:
            add_result(plot, kind, agent, used_colors[legend])
        
#     show(plot)
    return plot


    

In [4]:
def load_result_df(experiment):
    for basedir in basedirs:
        df = pd.DataFrame()
        try:
            path = os.path.join(basedir, experiment, 'results.csv')
            df = pd.read_csv(path, error_bad_lines=False)
        except Exception as e:
            print("Error in parsing result:", e)
            continue

    for col in df:
        df["".join(col.split()).lower()] = df[col]
#         df[col.strip().lower()] = df[col]
    df['experiment'] = pd.Series([experiment] * len(df), index=df.index)
    return df

def make_dataframe(results):
    data = pd.DataFrame()
    for experiment in results:
        single_df = load_result_df(experiment)
#         print(single_df)
        data = data.append(single_df, ignore_index=True)
#         print(data)
    return data

In [5]:
networks = [
    "breakout_skip5_z4_3e4_2",
    "breakout_skip5_z4_3e4_4",
    "breakout_skip5_z4_3e4_3",
    "breakout_skip5_z4_3e4_1",
]

data = make_dataframe(networks)
for facet in ['loss', 'trans divergence']:
    plot = Line(data, x='step', y=facet, 
                color=color(columns='experiment', palette=palettes.Spectral11),
                tools='pan,wheel_zoom,box_zoom,save,reset', 
                active_scroll="wheel_zoom",
                tooltips=tooltips,
                plot_width=900,
                plot_height=600)
    show(plot)

In [6]:
networks = [
    "urban_z4_3e5_1",
    "urban_z4_1e4_1",
    "urban_z4_3e4_1",
    "urban_z4_1e3_1",
]

data = make_dataframe(networks)
spaced_palette = palettes.linear_palette(palettes.Spectral11, len(networks))
for facet in ['loss', 'trans divergence']:
    plot = Line(data, x='step', y=facet, title="urban",
                color=color(columns='experiment', palette=spaced_palette),
                tools='pan,wheel_zoom,box_zoom,save,reset', 
                active_scroll="wheel_zoom",
                tooltips=tooltips,
                plot_width=900,
                plot_height=600)
    show(plot)

In [44]:
networks = [
#     "urban_128_z8_3e5_1",
#     "urban_128_z8_1e4_1",
#     "urban_128_z8_3e4_1",
#     "urban_128_z8_1e3_1",
#     "urban_128_dcgan_z8_3e5_1",
#     "urban_128_dcgan_z8_1e4_1",
    "urban_128_dcgan_z8_3e4_1",
    "urban_128_dcgan_z8_1e4_2",
    "urban_128_dcgan_z8_3e4_2",
#     "urban_128_dcgan_z8_3e5_1_restart",
#     "urban_128_dcgan_z8_1e4_1_restart",
#     "urban_128_dcgan_z8_3e4_1_restart",
    "urban_128_dcgan_z4_3e4_1",
    "urban_128_dcgan_z8_shallowtrans_3e4",
#     "urban_128_dcgan_z8_1e3_1",
]

palette = palettes.Spectral11[:5] + palettes.Spectral11[6:]
data = make_dataframe(networks)
spaced_palette = palettes.linear_palette(palette, len(networks))
for facet in ['loss', 'trans divergence']:
    plot = Line(data, x='step', y=facet, title="urban",
                color=color(columns='experiment', palette=spaced_palette),
                tools='pan,wheel_zoom,box_zoom,save,reset', 
                active_scroll="wheel_zoom",
                tooltips=tooltips,
                plot_width=900,
                plot_height=600,
                legend='top_right')
    if facet == 'loss':
        plot.y_range = bokeh.models.Range1d(-70000, -60000)
    elif facet == 'trans divergence':
        plot.y_range = bokeh.models.Range1d(20, 80)
    show(plot)